# Örnek 2

In [ ]:
# https://root.cern/doc/v628/rf107__plotstyles_8py.html

import ROOT
 
# Set up model
# ---------------------
 
# Create observables
x = ROOT.RooRealVar("x", "x", -10, 10)
 
# Create Gaussian
sigma = ROOT.RooRealVar("sigma", "sigma", 3, 0.1, 10)
mean = ROOT.RooRealVar("mean", "mean", -3, -10, 10)
gauss = ROOT.RooGaussian("gauss", "gauss", x, mean, sigma)
 
# Generate a sample of 100 events with sigma=3
data = gauss.generate({x}, 100)
 
# Fit pdf to data
gauss.fitTo(data, PrintLevel=-1)
 
# Make plot frames
# -------------------------------
 
# Make four plot frames to demonstrate various plotting features
frame1 = x.frame(Name="xframe", Title="Red Curve / SumW2 Histo errors", Bins=20)
frame2 = x.frame(Name="xframe", Title="Dashed Curve / No XError bars", Bins=20)
frame3 = x.frame(Name="xframe", Title="Filled Curve / Blue Histo", Bins=20)
frame4 = x.frame(Name="xframe", Title="Partial Range / Filled Bar chart", Bins=20)
 
# Data plotting styles
# ---------------------------------------
 
# Use sqrt(sum(weights^2)) error instead of Poisson errors
data.plotOn(frame1, DataError="SumW2")
 
# Remove horizontal error bars
data.plotOn(frame2, XErrorSize=0)
 
# Blue markers and error bors
data.plotOn(frame3, MarkerColor="b", LineColor="b")
 
# Filled bar chart
data.plotOn(frame4, DrawOption="B", DataError=None, XErrorSize=0, FillColor="kGray")
 
# Function plotting styles
# -----------------------------------------------
 
# Change line color to red
gauss.plotOn(frame1, LineColor="r")
 
# Change line style to dashed
gauss.plotOn(frame2, LineStyle="--")
 
# Filled shapes in green color
gauss.plotOn(frame3, MoveToBack=True, DrawOption="F", FillColor="kOrange")
 
#
gauss.plotOn(frame4, Range=(-8, 3), LineColor="m")
 
c = ROOT.TCanvas("rf107_plotstyles", "rf107_plotstyles", 800, 800)
c.Divide(2, 2)
c.cd(1)
ROOT.gPad.SetLeftMargin(0.15)
frame1.GetYaxis().SetTitleOffset(1.6)
frame1.Draw()
c.cd(2)
ROOT.gPad.SetLeftMargin(0.15)
frame2.GetYaxis().SetTitleOffset(1.6)
frame2.Draw()
c.cd(3)
ROOT.gPad.SetLeftMargin(0.15)
frame3.GetYaxis().SetTitleOffset(1.6)
frame3.Draw()
c.cd(4)
ROOT.gPad.SetLeftMargin(0.15)
frame4.GetYaxis().SetTitleOffset(1.6)
frame4.Draw()
 
c.SaveAs("rf107_plotstyles.png")

# Örnek 3

In [ ]:
# https://root.cern/doc/v628/rf109__chi2residpull_8py.html

from __future__ import print_function
import ROOT
 
# Set up model
# ---------------------
 
# Create observables
x = ROOT.RooRealVar("x", "x", -10, 10)
 
# Create Gaussian
sigma = ROOT.RooRealVar("sigma", "sigma", 3, 0.1, 10)
mean = ROOT.RooRealVar("mean", "mean", 0, -10, 10)
gauss = ROOT.RooGaussian("gauss", "gauss", x, mean, sigma)
 
# Generate a sample of 1000 events with sigma=3
data = gauss.generate({x}, 10000)
 
# Change sigma to 3.15
sigma.setVal(3.15)
 
# Plot data and slightly distorted model
# ---------------------------------------------------------------------------
 
# Overlay projection of gauss with sigma=3.15 on data with sigma=3.0
frame1 = x.frame(Title="Data with distorted Gaussian pdf", Bins=40)
data.plotOn(frame1, DataError="SumW2")
gauss.plotOn(frame1)
 
# Calculate chi^2
# ------------------------------
 
# Show the chi^2 of the curve w.r.t. the histogram
# If multiple curves or datasets live in the frame you can specify
# the name of the relevant curve and/or dataset in chiSquare()
print("chi^2 = ", frame1.chiSquare())
 
# Show residual and pull dists
# -------------------------------------------------------
 
# Construct a histogram with the residuals of the data w.r.t. the curve
hresid = frame1.residHist()
 
# Construct a histogram with the pulls of the data w.r.t the curve
hpull = frame1.pullHist()
 
# Create a frame to draw the residual distribution and add the
# distribution to the frame
frame2 = x.frame(Title="Residual Distribution")
frame2.addPlotable(hresid, "P")
 
# Create a frame to draw the pull distribution and add the distribution to
# the frame
frame3 = x.frame(Title="Pull Distribution")
frame3.addPlotable(hpull, "P")
 
c = ROOT.TCanvas("rf109_chi2residpull", "rf109_chi2residpull", 900, 300)
c.Divide(3)
c.cd(1)
ROOT.gPad.SetLeftMargin(0.15)
frame1.GetYaxis().SetTitleOffset(1.6)
frame1.Draw()
c.cd(2)
ROOT.gPad.SetLeftMargin(0.15)
frame2.GetYaxis().SetTitleOffset(1.6)
frame2.Draw()
c.cd(3)
ROOT.gPad.SetLeftMargin(0.15)
frame3.GetYaxis().SetTitleOffset(1.6)
frame3.Draw()
 
c.SaveAs("rf109_chi2residpull.png")

# Örnek 4

In [ ]:
# https://root.cern/doc/v628/rf312__multirangefit_8py.html

import ROOT
 
# Create 2D pdf and data
# -------------------------------------------
 
# Define observables x,y
x = ROOT.RooRealVar("x", "x", -10, 10)
y = ROOT.RooRealVar("y", "y", -10, 10)
 
# Construct the signal pdf gauss(x)*gauss(y)
mx = ROOT.RooRealVar("mx", "mx", 1, -10, 10)
my = ROOT.RooRealVar("my", "my", 1, -10, 10)
 
gx = ROOT.RooGaussian("gx", "gx", x, mx, ROOT.RooFit.RooConst(1))
gy = ROOT.RooGaussian("gy", "gy", y, my, ROOT.RooFit.RooConst(1))
 
sig = ROOT.RooProdPdf("sig", "sig", gx, gy)
 
# Construct the background pdf (flat in x,y)
px = ROOT.RooPolynomial("px", "px", x)
py = ROOT.RooPolynomial("py", "py", y)
bkg = ROOT.RooProdPdf("bkg", "bkg", px, py)
 
# Construct the composite model sig+bkg
f = ROOT.RooRealVar("f", "f", 0.0, 1.0)
model = ROOT.RooAddPdf("model", "model", [sig, bkg], [f])
 
# Sample 10000 events in (x,y) from the model
modelData = model.generate({x, y}, 10000)
 
# Define signal and sideband regions
# -------------------------------------------------------------------
 
# Construct the SideBand1,SideBand2, regions
#
#                    |
#      +-------------+-----------+
#      |             |           |
#      |    Side     |   Sig     |
#      |    Band1    |   nal     |
#      |             |           |
#    --+-------------+-----------+--
#      |                         |
#      |           Side          |
#      |           Band2         |
#      |                         |
#      +-------------+-----------+
#                    |
 
x.setRange("SB1", -10, +10)
y.setRange("SB1", -10, 0)
 
x.setRange("SB2", -10, 0)
y.setRange("SB2", 0, +10)
 
x.setRange("SIG", 0, +10)
y.setRange("SIG", 0, +10)
 
x.setRange("FULL", -10, +10)
y.setRange("FULL", -10, +10)
 
# Perform fits in individual sideband regions
# -------------------------------------------------------------------------------------
 
# Perform fit in SideBand1 region (ROOT.RooAddPdf coefficients will be
# interpreted in full range)
r_sb1 = model.fitTo(modelData, Range="SB1", Save=True, PrintLevel=-1)
 
# Perform fit in SideBand2 region (ROOT.RooAddPdf coefficients will be
# interpreted in full range)
r_sb2 = model.fitTo(modelData, Range="SB2", Save=True, PrintLevel=-1)
 
# Perform fits in joint sideband regions
# -----------------------------------------------------------------------------
 
# Now perform fit to joint 'L-shaped' sideband region 'SB1|SB2'
# (ROOT.RooAddPdf coefficients will be interpreted in full range)
r_sb12 = model.fitTo(modelData, Range="SB1,SB2", Save=True, PrintLevel=-1)
 
# Print results for comparison
r_sb1.Print()
r_sb2.Print()
r_sb12.Print()